In [7]:
import os, glob, re, time
import pandas as pd
from tensorboard.backend.event_processing.event_accumulator import EventAccumulator

target_dir = '/home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/'
tag =  "Episode_Reward/termination_penalty"
def find_run_dirs(logdir):
    """Return directories that contain at least one .tfevents file."""
    run_dirs = set()
    for root, _, _ in os.walk(logdir):
        if glob.glob(os.path.join(root, "*.tfevents.*")):
            run_dirs.add(root)
    # Stable order
    return sorted(run_dirs)


def choose_tag(ea, wanted):
    """Pick the best-matching tag present in this run."""
    tags = set(ea.Tags().get("scalars", []))
    if wanted in tags:
        return wanted
    # Be forgiving: allow leading/trailing slashes or suffix matches
    candidates = []
    wanted_base = wanted.strip("/")
    for t in tags:
        if t.strip("/") == wanted_base or t.endswith("/" + wanted_base) or t == wanted_base:
            candidates.append(t)
    return candidates[0] if candidates else None


def last_point(ea, tag):
    vals = ea.Scalars(tag)
    if not vals:
        return None
    v = vals[-1]  # last logged point
    return {"step": v.step, "value": float(v.value), "wall_time": float(v.wall_time)}

rows = []

# run_dirs = find_run_dirs(dir)
# print(run_dirs)
run_dirs = find_run_dirs(target_dir)
total = len(run_dirs)
for i, run_dir in enumerate(run_dirs):
    try:
        print(f"run_dir {i+1} of {total}:", run_dir)
        ea = EventAccumulator(
            run_dir,
            size_guidance={"scalars": 10_000}  # bump if you log a lot
        )
        ea.Reload()
        tag = choose_tag(ea, tag)
        if not tag:
            continue
        lp = last_point(ea, tag)
        if not lp:
            continue
        rows.append({
            "run_dir": run_dir,
            "run_name": os.path.basename(run_dir),
            "tag": tag,
            **lp
        })
    except Exception as e:
        # Skip corrupt/incomplete runs gracefully
        print(f"[warn] {run_dir}: {e}")

#     if not rows:
#         print("No matching scalars found.")
#         return

run_dir 1 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/2025-10-02_14-31-47_T_12
run_dir 2 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/2025-10-02_15-00-54_fqs9
run_dir 3 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/2025-10-02_15-29-46_8cvb
run_dir 4 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/2025-10-02_15-57-28_yf_N
run_dir 5 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/2025-10-02_16-25-04_eQxo
run_dir 6 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/2025-10-02_16-52-30_LFqJ
run_dir 7 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/2025-10-02_17-20-08_TIfd
run_dir 8 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/2025-10-02_17-47-31_xWCc
run_dir 9 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/2025-10-02_18-14-45_68Id
run_dir 10 of 27: /home/logan/Projects/g1_crawl/logs/rsl_rl/g1_s

In [3]:
from tensorboard.backend.event_processing.event_multiplexer import EventMultiplexer
import os, glob, pandas as pd

# Build a dict of run_name -> directory
def run_map(logdir):
    mapping = {}
    for root, _, _ in os.walk(logdir):
        if glob.glob(os.path.join(root, "*.tfevents.*")):
            mapping[os.path.basename(root)] = root
    return mapping

print("Starting")
LOGDIR =  '/home/logan/Projects/g1_crawl/logs/rsl_rl/g1_shamble_sweep_v4/'
mux = EventMultiplexer(run_map(LOGDIR), size_guidance={
    "scalars": 100000, "histograms": 0, "images": 0, "tensors": 0
})

print("mux completed")
mux.Reload()   # one-time cost
print("reloaded")
rows = []
total = len(mux.Runs())
for i, run_name in enumerate(mux.Runs()):
    print(f"run {i+1} of {total}")
    if "Episode_Reward/termination_penalty" not in mux.Tags(run_name).get("scalars", []):
        continue
    vals = mux.Scalars(run_name, "Episode_Reward/termination_penalty")
    if vals:
        last = vals[-1]
        rows.append({
            "run": run_name,
            "step": last.step,
            "value": last.value,
            "wall_time": last.wall_time
        })

df = pd.DataFrame(rows).sort_values("value", ascending=False)
print(df)


Starting
mux completed
reloaded
run 1 of 27


AttributeError: 'EventMultiplexer' object has no attribute 'Tags'

In [ ]:
runs = list(mux.Runs())
total = len(runs)

print(f"Processing {total} runs for 'Episode_Reward/termination_penalty'...\n")

tag = 

for i, run_name in enumerate(runs, 1):
    print(f"[{i}/{total}] {run_name[:60]}...", end=" ")
    vals = mux.Scalars(run_name, "Episode_Reward/termination_penalty")
    assert vals is not None, f"No values found for 'Episode_Reward/termination_penalty' in run {run_name}"
    if vals:
        last = vals[-1]
        rows.append({
            "run": run_name,
            "step": last.step,
            "value": last.value,
            "wall_time": last.wall_time
        })
        print(f"✓ (last value: {last.value:.4f} at step {last.step})")

Processing 27 runs for 'Episode_Reward/termination_penalty'...

[1/27] 2025-10-03_02-02-45_D9mU... [ScalarEvent(wall_time=1759482173.130692, step=0, value=-0.05412064120173454), ScalarEvent(wall_time=1759482173.7819266, step=1, value=-0.20000001788139343), ScalarEvent(wall_time=1759482174.4137409, step=2, value=-0.20000001788139343), ScalarEvent(wall_time=1759482175.0424144, step=3, value=-0.20000001788139343), ScalarEvent(wall_time=1759482175.6581056, step=4, value=-0.19999998807907104), ScalarEvent(wall_time=1759482176.305913, step=5, value=-0.19999998807907104), ScalarEvent(wall_time=1759482176.9535642, step=6, value=-0.19999998807907104), ScalarEvent(wall_time=1759482177.606222, step=7, value=-0.20000001788139343), ScalarEvent(wall_time=1759482178.2332673, step=8, value=-0.19999998807907104), ScalarEvent(wall_time=1759482178.8740518, step=9, value=-0.19999998807907104), ScalarEvent(wall_time=1759482179.5101368, step=10, value=-0.19999998807907104), ScalarEvent(wall_time=1759482180.

In [8]:
tag_map

{}